In [1]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json
from geopy.geocoders import Nominatim
import requests
from pandas.io.json import json_normalize

import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans

import folium
import warnings
warnings.filterwarnings("ignore")
print('Libraries imported.')

Libraries imported.


In [2]:
df_wiki = pd.read_html('https://en.wikipedia.org/wiki/List_of_areas_of_London')

In [3]:
london = df_wiki[1]
london

Location  \
0                                        Abbey Wood   
1                                             Acton   
2                                         Addington   
3                                        Addiscombe   
4                                       Albany Park   
5                                  Aldborough Hatch   
6                                           Aldgate   
7                                           Aldwych   
8                                          Alperton   
9                                           Anerley   
10                                            Angel   
11                                        Aperfield   
12                                          Archway   
13                                   Ardleigh Green   
14                                           Arkley   
15                                      Arnos Grove   
16                                           Balham   
17                                         Bankside   
18                                         Barbican   
19                                          Barking   
20                                      Barkingside   
21                                       Barnehurst   
22                                           Barnes   
23                                      Barnes Cray   
24                                      Barnet Gate   
25       Barnet (also Chipping Barnet, High Barnet)   
26                                        Barnsbury   
27                                        Battersea   
28                                        Bayswater   
29                                        Beckenham   
30                                          Beckton   
31                                        Becontree   
32                                  Becontree Heath   
33                                       Beddington   
34                                     Bedford Park   
35                                        Belgravia   
36                                       Bellingham   
37                                          Belmont   
38                                          Belmont   
39                                     Belsize Park   
40                                        Belvedere   
41                                       Bermondsey   
42                                       Berrylands   
43                                    Bethnal Green   
44         Bexley (also Old Bexley, Bexley Village)   
45               Bexleyheath (also Bexley New Town)   
46                                          Bickley   
47                                      Biggin Hill   
48                                         Blackfen   
49                                      Blackfriars   
50                                       Blackheath   
51                        Blackheath Royal Standard   
52                                        Blackwall   
53                                          Blendon   
54                                       Bloomsbury   
55                                       Botany Bay   
56                                     Bounds Green   
57                                              Bow   
58                                       Bowes Park   
59                                        Brentford   
60                                      Brent Cross   
61                                       Brent Park   
62                                        Brimsdown   
63                                          Brixton   
64                                         Brockley   
65                                          Bromley   
66                    Bromley (also Bromley-by-Bow)   
67                                   Bromley Common   
68                                         Brompton   
69                                      Brondesbury   
70                                   Brunswick Park   
71                                      Bulls Cross   
72                          

In [4]:
london = london.iloc[:,[0,1,2]]
london.head()

Location                     London borough       Post town
0   Abbey Wood              Bexley, Greenwich [7]          LONDON
1        Acton  Ealing, Hammersmith and Fulham[8]          LONDON
2    Addington                         Croydon[8]         CROYDON
3   Addiscombe                         Croydon[8]         CROYDON
4  Albany Park                             Bexley  BEXLEY, SIDCUP

In [5]:
london.columns = ['Neighborhood','Borough','Post town']

In [6]:
london_data = pd.DataFrame()
for index , row in london.iterrows():
    if row['Post town'].find('LONDON')!=-1:
        if row['Borough'].find('[')==-1:
            london_data = london_data.append(row)
        else:
            1
london_data.reset_index(drop=True,inplace=True)

In [7]:
london_data.head()

Borough               Neighborhood       Post town
0     Barnet                Barnet Gate  LONDON, BARNET
1  Greenwich  Blackheath Royal Standard          LONDON
2     Barnet                Brent Cross          LONDON
3      Brent                 Brent Park          LONDON
4   Lewisham                    Catford          LONDON

In [8]:
# london['Borough'].value_counts()

In [9]:
london_data['latitude'] = 0.0
london_data['longitude'] = 0.0
london_data.head()

Borough               Neighborhood       Post town  latitude  longitude
0     Barnet                Barnet Gate  LONDON, BARNET       0.0        0.0
1  Greenwich  Blackheath Royal Standard          LONDON       0.0        0.0
2     Barnet                Brent Cross          LONDON       0.0        0.0
3      Brent                 Brent Park          LONDON       0.0        0.0
4   Lewisham                    Catford          LONDON       0.0        0.0

In [10]:
geolocator = Nominatim(user_agent="ny_explorer")

In [11]:
indices_drop =[]
for index, row in london_data.iterrows():
    address =london_data['Neighborhood'][index]+', '+ london_data['Post town'][index]
#     print(address)
    location = geolocator.geocode(address)
#     print(location.latitude)
    try:
        latitude = location.latitude
        longitude = location.longitude
        london_data['latitude'][index] = latitude
        london_data['longitude'][index] = longitude
    except:
        indices_drop.append(index)

In [12]:
print(indices_drop)
print(london_data.shape)
london_data.head()

[125, 169, 185, 212, 215]
(263, 5)


Borough               Neighborhood       Post town   latitude  longitude
0     Barnet                Barnet Gate  LONDON, BARNET  51.641827  -0.242985
1  Greenwich  Blackheath Royal Standard          LONDON  51.477735   0.020490
2     Barnet                Brent Cross          LONDON  51.576760  -0.218380
3      Brent                 Brent Park          LONDON  51.563826  -0.275760
4   Lewisham                    Catford          LONDON  51.445321  -0.019753

In [13]:
london_data.drop(index = indices_drop,inplace = True)
london_data.shape

(258, 5)

In [14]:
london_address = 'London, United Kingdom'
location = geolocator.geocode(address)
london_latitude = location.latitude
london_longitude = location.longitude
print('The coordinates of London are {} , {}'.format(london_latitude,london_longitude))

The coordinates of London are 51.52137985 , -0.24043929057201105


In [16]:
map_london = folium.Map(location=[london_latitude,london_longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(london_data['latitude'], london_data['longitude'], london_data['Borough'], london_data['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_london)  
    
map_london

In [17]:
CLIENT_ID = 'B0MWNNRJM5A4AEKPTTQKHDBWWAZF4MGKIESUMLTJOUPGQSED' # your Foursquare ID
CLIENT_SECRET = 'HH5LLRRQEEPEXL4FDETHRBNCFDCTQW5GIPVY5OY0NKONEIVW' # your Foursquare Secret
VERSION = '20200606' # Foursquare API version
LIMIT= 100
radius = 600
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: B0MWNNRJM5A4AEKPTTQKHDBWWAZF4MGKIESUMLTJOUPGQSED
CLIENT_SECRET:HH5LLRRQEEPEXL4FDETHRBNCFDCTQW5GIPVY5OY0NKONEIVW


In [18]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        try:
            results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
            venues_list.append([(
                name, 
                lat, 
                lng, 
                v['venue']['name'], 
                v['venue']['location']['lat'], 
                v['venue']['location']['lng'],  
                v['venue']['categories'][0]['name']) for v in results])
        except:
            1

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [19]:
# london_venues = None
london_venues = getNearbyVenues(names=london_data['Neighborhood'],
                                   latitudes=london_data['latitude'],
                                   longitudes=london_data['longitude']
                                  )
# print(london_venues)

Barnet Gate
Blackheath Royal Standard
Brent Cross
Brent Park
Catford
Chalk Farm
Charing Cross
Charlton
Chelsea
Childs Hill
Chinatown
Chinbrook
Chingford
Chiswick
Church End
Church End
Clapham
Clerkenwell
Colindale
Colliers Wood
Colney Hatch
Covent Garden
Cricklewood
Crofton Park
Crossness
Crouch End
Crystal Palace
Cubitt Town
Custom House
Dalston
Dartford
De Beauvoir Town
Denmark Hill
Deptford
Dollis Hill
Dulwich
Ealing
Earls Court
Earlsfield
East Dulwich
East Finchley
East Ham
East Sheen
Edmonton
Elephant and Castle
Eltham
Falconwood
Farringdon
Finchley
Finsbury
Finsbury Park
Fitzrovia
Forest Gate
Forest Hill
Fortis Green
Friern Barnet
Frognal
Fulham
Gipsy Hill
Golders Green
Gospel Oak
Grahame Park
Grange Park
Greenwich
Grove Park
Grove Park
Gunnersbury
Hackney
Hackney Central
Hackney Marshes
Hackney Wick
Haggerston
The Hale
Hammersmith
Hampstead
Hampstead Garden Suburb
Hanwell
Harlesden
Harringay
Hendon
Herne Hill
Highams Park
Highbury
Highgate
Hither Green
Holborn
Holland Park
Hollo

In [20]:
print(london_venues.shape)
london_venues.head()

(7602, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0                Barnet Gate              51.641827               -0.242985   
1                Barnet Gate              51.641827               -0.242985   
2                Barnet Gate              51.641827               -0.242985   
3  Blackheath Royal Standard              51.477735                0.020490   
4  Blackheath Royal Standard              51.477735                0.020490   

                   Venue  Venue Latitude  Venue Longitude  \
0               The Gate       51.641994        -0.242582   
1              Hadley FC       51.642660        -0.243032   
2       Barnet Gate Wood       51.639062        -0.242836   
3  Mara Interiors & Café       51.477672         0.019368   
4        M&S Simply Food       51.476772         0.020189   

           Venue Category  
0                     Pub  
1            Soccer Field  
2                  Forest  
3  Furniture / Home Store  
4           Grocery Store

In [21]:
london_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Barnet Gate                                    3                       3   
Blackheath Royal Standard                     10                      10   
Brent Cross                                   48                      48   
Brent Park                                    16                      16   
Catford                                       31                      31   
Chalk Farm                                    83                      83   
Charing Cross                                 46                      46   
Charlton                                      11                      11   
Chelsea                                       44                      44   
Childs Hill                                    6                       6   
Chinatown                                    100                     100   
Chinbrook                                      2                       2   
Chingford                                     12                      12   
Chiswick                                      58                      58   
Church End                                    62                      62   
Clapham                                       90                      90   
Clerkenwell                                  100                     100   
Colindale                                     12                      12   
Colliers Wood                                 25                      25   
Colney Hatch                                   4                       4   
Covent Garden                                 89                      89   
Cricklewood                                   32                      32   
Crofton Park                                  17                      17   
Crossness                                      1                       1   
Crouch End                                    69                      69   
Crystal Palace                                22                      22   
Cubitt Town                                   17                      17   
Custom House                                  44                      44   
Dalston                                       15                      15   
Dartford                                      31                      31   
De Beauvoir Town                              22                      22   
Denmark Hill                                  17                      17   
Deptford                                      51                      51   
Dollis Hill                                    6                       6   
Dulwich                                        7                       7   
Ealing                                        95                      95   
Earls Court                                   65                      65   
Earlsfield                                    15                      15   
East Dulwich                                  43                      43   
East Finchley                                 36                      36   
East Ham                                      15                      15   
East Sheen                                    24                      24   
Edmonton                                      11                      11   
Elephant and Castle                           45                      45   
Eltham                                        31                      31   
Falconwood                                     4                       4   
Farringdon                                    53                      53   
Finchley                                       5                       5   
Fitzrovia                                     62                      62   
Forest Gate                                   15                      15   
Forest Hill                                   23                      23   

In [22]:
print('There are {} uniques categories.'.format(len(london_venues['Venue Category'].unique())))

There are 380 uniques categories.


In [23]:
# one hot encoding
london_onehot = pd.get_dummies(london_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
london_onehot['Neighborhood'] = london_venues['Neighborhood'] 

# move neighborhood column to the first column
# fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
# london_onehot = london_onehot[fixed_columns]

In [24]:
london_onehot.head()

Accessories Store  Advertising Agency  Afghan Restaurant  \
0                  0                   0                  0   
1                  0                   0                  0   
2                  0                   0                  0   
3                  0                   0                  0   
4                  0                   0                  0   

   African Restaurant  Airport Lounge  Airport Terminal  American Restaurant  \
0                   0               0                 0                    0   
1                   0               0                 0                    0   
2                   0               0                 0                    0   
3                   0               0                 0                    0   
4                   0               0                 0                    0   

   Antique Shop  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0             0       0                 0                       0   
1             0       0                 0                       0   
2             0       0                 0                       0   
3             0       0                 0                       0   
4             0       0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Athletics & Sports  Australian Restaurant  \
0                 0                   0                      0   
1                 0                   0                      0   
2                 0                   0                      0   
3                 0                   0                      0   
4                 0                   0                      0   

   Austrian Restaurant  Auto Dealership  Auto Garage  BBQ Joint  Baby Store  \
0                    0                0            0          0           0   
1                    0                0            0          0           0   
2                    0                0            0          0           0   
3                    0                0            0          0           0   
4                    0                0            0          0           0   

   Bagel Shop  Bakery  Bar  Baseball Field  Bathing Area  Beach  \
0           0       0    0               0             0      0   
1           0       0    0               0             0      0   
2           0       0    0               0             0      0   
3           0       0    0               0             0      0   
4           0       0    0               0             0      0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Belgian Restaurant  \
0                0         0            0           0                   0   
1                0         0            0           0                   0   
2                0         0            0           0                   0   
3                0         0            0           0                   0   
4                0         0            0           0                   0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Boarding House  \
0                         0          0           0       0               0   
1                         0          0           0       0               0   
2                         0          0           0       0               0   
3                         0          0           0       0               0   
4                         0          0           0       0               0   

   Boat or Ferry  Bookstore  Border Crossing  Boutique  Bowling Alley  \
0        

In [25]:
london_grouped = london_onehot.groupby('Neighborhood').mean().reset_index()
london_grouped

Neighborhood  Accessories Store  Advertising Agency  \
0                  Barnet Gate           0.000000               0.000   
1    Blackheath Royal Standard           0.000000               0.000   
2                  Brent Cross           0.020833               0.000   
3                   Brent Park           0.000000               0.000   
4                      Catford           0.000000               0.000   
5                   Chalk Farm           0.000000               0.000   
6                Charing Cross           0.000000               0.000   
7                     Charlton           0.000000               0.000   
8                      Chelsea           0.000000               0.000   
9                  Childs Hill           0.000000               0.000   
10                   Chinatown           0.000000               0.000   
11                   Chinbrook           0.000000               0.000   
12                   Chingford           0.000000               0.000   
13                    Chiswick           0.000000               0.000   
14                  Church End           0.000000               0.000   
15                     Clapham           0.000000               0.000   
16                 Clerkenwell           0.000000               0.000   
17                   Colindale           0.000000               0.000   
18               Colliers Wood           0.000000               0.000   
19                Colney Hatch           0.000000               0.000   
20               Covent Garden           0.000000               0.000   
21                 Cricklewood           0.000000               0.000   
22                Crofton Park           0.000000               0.000   
23                   Crossness           0.000000               0.000   
24                  Crouch End           0.000000               0.000   
25              Crystal Palace           0.000000               0.000   
26                 Cubitt Town           0.000000               0.000   
27                Custom House           0.000000               0.000   
28                     Dalston           0.000000               0.000   
29                    Dartford           0.000000               0.000   
30            De Beauvoir Town           0.000000               0.000   
31                Denmark Hill           0.000000               0.000   
32                    Deptford           0.000000               0.000   
33                 Dollis Hill           0.000000               0.000   
34                     Dulwich           0.000000               0.000   
35                      Ealing           0.000000               0.000   
36                 Earls Court           0.000000               0.000   
37                  Earlsfield           0.000000               0.000   
38                East Dulwich           0.000000               0.000   
39               East Finchley           0.000000               0.000   
40                    East Ham           0.000000               0.000   
41                  East Sheen           0.000000               0.000   
42                    Edmonton           0.000000               0.000   
43         Elephant and Castle           0.000000               0.000   
44                      Eltham           0.000000               0.000   
45                  Falconwood           0.000000               0.000   
46                  Farringdon           0.000000               0.000   
47                    Finchley           0.000000               0.000   
48                   Fitzrovia           0.000000               0.000   
49                 Forest Gate           0.000000               0.000   
50                 Forest Hill           0.000000               0.000   
51                Fortis Green           0.000000               0.000   
52               Friern Barnet           0.000000               0.000   
53                     Frognal           0.000000               0.000   
54 

In [26]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [27]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = london_grouped['Neighborhood']

for ind in np.arange(london_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(london_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0                Barnet Gate                Forest          Soccer Field   
1  Blackheath Royal Standard                   Pub    Chinese Restaurant   
2                Brent Cross        Clothing Store           Coffee Shop   
3                 Brent Park           Coffee Shop                 Hotel   
4                    Catford           Supermarket         Grocery Store   

  3rd Most Common Venue 4th Most Common Venue   5th Most Common Venue  \
0                   Pub         Indie Theater    Fast Food Restaurant   
1         Grocery Store              Bus Stop  Furniture / Home Store   
2                  Café      Department Store           Women's Store   
3           Supermarket            Food Court       Electronics Store   
4    Italian Restaurant         Train Station             Coffee Shop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0     Electronics Store    English Restaurant  Ethiopian Restaurant   
1                  Café           Rugby Pitch  Fast Food Restaurant   
2           Supermarket           Men's Store     Electronics Store   
3      Pedestrian Plaza              Platform                  Café   
4              Platform              Pharmacy                   Pub   

  9th Most Common Venue 10th Most Common Venue  
0           Event Space                Exhibit  
1           Zoo Exhibit                   Farm  
2            Shoe Store      Accessories Store  
3          Burger Joint             Sports Bar  
4          Cocktail Bar  Portuguese Restaurant

In [28]:
from sklearn.cluster import KMeans
# set number of clusters
kclusters = 14
london_grouped_clustering = london_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(london_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([12,  4, 11, 11,  1, 11, 11,  5, 11,  8])

In [29]:
# add clustering labels
# try:
#     neighborhoods_venues_sorted.drop(['Cluster Labels'])
try:
    neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
except:
    neighborhoods_venues_sorted['Cluster Labels'] = kmeans.labels_
london_merged = london_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
london_merged = london_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

london_merged.head() # check the last columns!

Borough               Neighborhood       Post town   latitude  longitude  \
0     Barnet                Barnet Gate  LONDON, BARNET  51.641827  -0.242985   
1  Greenwich  Blackheath Royal Standard          LONDON  51.477735   0.020490   
2     Barnet                Brent Cross          LONDON  51.576760  -0.218380   
3      Brent                 Brent Park          LONDON  51.563826  -0.275760   
4   Lewisham                    Catford          LONDON  51.445321  -0.019753   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0            12.0                Forest          Soccer Field   
1             4.0                   Pub    Chinese Restaurant   
2            11.0        Clothing Store           Coffee Shop   
3            11.0           Coffee Shop                 Hotel   
4             1.0           Supermarket         Grocery Store   

  3rd Most Common Venue 4th Most Common Venue   5th Most Common Venue  \
0                   Pub         Indie Theater    Fast Food Restaurant   
1         Grocery Store              Bus Stop  Furniture / Home Store   
2                  Café      Department Store           Women's Store   
3           Supermarket            Food Court       Electronics Store   
4    Italian Restaurant         Train Station             Coffee Shop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0     Electronics Store    English Restaurant  Ethiopian Restaurant   
1                  Café           Rugby Pitch  Fast Food Restaurant   
2           Supermarket           Men's Store     Electronics Store   
3      Pedestrian Plaza              Platform                  Café   
4              Platform              Pharmacy                   Pub   

  9th Most Common Venue 10th Most Common Venue  
0           Event Space                Exhibit  
1           Zoo Exhibit                   Farm  
2            Shoe Store      Accessories Store  
3          Burger Joint             Sports Bar  
4          Cocktail Bar  Portuguese Restaurant

In [30]:
london_merged['Cluster Labels'].dropna(inplace=True)
london_merged['Cluster Labels'].value_counts()

11.0    66
3.0     63
8.0     36
1.0     23
5.0     20
4.0     20
0.0     10
2.0      5
6.0      3
12.0     3
7.0      2
10.0     1
13.0     1
9.0      1
Name: Cluster Labels, dtype: int64

In [82]:
import matplotlib.cm as cm
import matplotlib.colors as colors

# create map
map_clusters = folium.Map(location=[london_latitude, london_longitude +0.2], zoom_start=10.6)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(london_merged['latitude'], london_merged['longitude'], london_merged['Neighborhood'], london_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color='black',
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.9).add_to(map_clusters)
       
map_clusters

In [55]:
pd.set_option('display.width',1000)
pd.set_option('display.max_columns',1000)

In [63]:
onlyclusters = london_merged.loc[:,london_merged.columns[[1] + list(range(5,london_merged.shape[1]))]]

In [67]:
onlyclusters[onlyclusters['Cluster Labels']==0]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue 7th Most Common Venue 8th Most Common Venue 9th Most Common Venue       10th Most Common Venue
26   Crystal Palace             0.0              Platform     Outdoor Sculpture  Gym / Fitness Center          Track Stadium         Train Station                Garden    Athletics & Sports           Coffee Shop             Bike Shop               History Museum
64       Grove Park             0.0              Platform         Grocery Store    Chinese Restaurant                   Park                   Pub     Indian Restaurant   Fried Chicken Joint         Train Station           Coffee Shop           Falafel Restaurant
65       Grove Park             0.0              Platform         Grocery Store    Chinese Restaurant                   Park                   Pub     Indian Restaurant   Fried Chicken Joint         Train Station           Coffee Shop           Falafel Restaurant
84     Hither Green             0.0              Platform                  Café         Grocery Store      Fish & Chips Shop  Gym / Fitness Center           Coffee Shop           Social Club   Fried Chicken Joint             Gastropub                         Park
89        Honor Oak             0.0              Platform                  Café        Scenic Lookout                 Garden           Pizza Place           Zoo Exhibit  Ethiopian Restaurant           Event Space               Exhibit                  Fabric Shop
131       Mill Hill             0.0     Convenience Store    Athletics & Sports           Zoo Exhibit    Filipino Restaurant  Ethiopian Restaurant           Event Space               Exhibit           Fabric Shop    Falafel Restaurant                         Farm
152  Old Oak Common             0.0              Platform     Electronics Store                  Café     Spanish Restaurant              Bus Stop           Event Space               Exhibit           Fabric Shop    Falafel Restaurant                         Farm
188   South Norwood             0.0              Platform           Coffee Shop                  Café                    Pub           Supermarket                  Park           Gas Station           Zoo Exhibit    English Restaurant         Ethiopian Restaurant
224      Tulse Hill             0.0              Platform           Coffee Shop                   Pub  Portuguese Restaurant       Thai Restaurant                 Hotel         Train Station         Grocery Store    Falafel Restaurant  Eastern European Restaurant
243        West Ham             0.0              Platform     Fish & Chips Shop                  Café                  Trail           Bus Station         Metro Station                  Park        Farmers Market  Ethiopian Restaurant                  Event Space

In [68]:
onlyclusters[onlyclusters['Cluster Labels']==1]

Neighborhood  Cluster Labels   1st Most Common Venue 2nd Most Common Venue  3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue 6th Most Common Venue       7th Most Common Venue   8th Most Common Venue 9th Most Common Venue     10th Most Common Venue
4            Catford             1.0             Supermarket         Grocery Store     Italian Restaurant         Train Station            Coffee Shop              Platform                    Pharmacy                     Pub          Cocktail Bar      Portuguese Restaurant
18         Colindale             1.0             Supermarket  Gym / Fitness Center               Bus Stop    Chinese Restaurant          Metro Station           Coffee Shop                        Park             Pizza Place         Grocery Store                        Pub
20      Colney Hatch             1.0  College Football Field           Auto Garage               Bus Stop           Pizza Place    Filipino Restaurant           Event Space                     Exhibit             Fabric Shop    Falafel Restaurant                       Farm
34       Dollis Hill             1.0                  Bakery  Fast Food Restaurant  Portuguese Restaurant         Metro Station             Restaurant                Hostel          English Restaurant    Ethiopian Restaurant           Event Space                    Exhibit
48          Finchley             1.0                 Gay Bar         Moving Target   Gym / Fitness Center  Fast Food Restaurant                Brewery            Food Court                  Food Stand             Event Space      Football Stadium                    Exhibit
62       Grange Park             1.0      English Restaurant         Train Station      Indian Restaurant           Golf Course                  Field  Ethiopian Restaurant                 Event Space                 Exhibit           Fabric Shop         Falafel Restaurant
101        Kidbrooke             1.0             Rugby Pitch              Bus Stop            Supermarket                  Park                   Café           Zoo Exhibit        Fast Food Restaurant    Ethiopian Restaurant           Event Space                    Exhibit
119        Longlands             1.0      Italian Restaurant     Indian Restaurant                 Bakery      Dentist's Office    Rental Car Location  Gym / Fitness Center  Construction & Landscaping          Farmers Market            Food Stand         English Restaurant
130         Mile End             1.0                Bus Stop                   Pub            Coffee Shop           Pizza Place               Platform          Burger Joint               Grocery Store              Canal Lock        Breakfast Spot                       Park
133         Millwall             1.0                Bus Stop                   Bar      Indian Restaurant     Convenience Store        Harbor / Marina     Korean Restaurant                     Theater                     Gym              Gym Pool  Middle Eastern Restaurant
135       Mottingham             1.0                     Gym     Convenience Store              Pet Store                   Bar            Zoo Exhibit  Fast Food Restaurant        Ethiopian Restaurant             Event Space               Exhibit                Fabric Shop
138          Neasden             1.0   Portuguese Restaurant        Sandwich Place          Metro Station              Bus Stop            Supermarket           Zoo Exhibit        Fast Food Restaurant    Ethiopian Restaurant           Event Space                    Exhibit
140       New Eltham             1.0                     Bar                 Hotel          Grocery Store       Auto Dealership      Indian Restaurant      Kebab Restaurant                    Bus Stop    Fast Food Restaurant           Auto Garage                   Platform
143        Nine Elms             1.0    Gym / Fitness Center                   Bar            Coffee Shop           Pizza Place  Performing Arts Venue           Supermarket

In [69]:
onlyclusters[onlyclusters['Cluster Labels']==2]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue        4th Most Common Venue 5th Most Common Venue 6th Most Common Venue 7th Most Common Venue 8th Most Common Venue 9th Most Common Venue 10th Most Common Venue
11                 Chinbrook             2.0          Soccer Field                  Park           Zoo Exhibit         Ethiopian Restaurant           Event Space               Exhibit           Fabric Shop    Falafel Restaurant                  Farm         Farmers Market
75   Hampstead Garden Suburb             2.0                  Park           Coffee Shop           Zoo Exhibit            Electronics Store  Ethiopian Restaurant           Event Space               Exhibit           Fabric Shop    Falafel Restaurant                   Farm
110                 Leamouth             2.0                  Park     Convenience Store                  Farm                     Bus Stop           Zoo Exhibit   Filipino Restaurant           Event Space               Exhibit           Fabric Shop     Falafel Restaurant
128              Merton Park             2.0           Sports Club                  Park           Zoo Exhibit                        Field  Ethiopian Restaurant           Event Space               Exhibit           Fabric Shop    Falafel Restaurant                   Farm
261                 Woolwich             2.0                  Park    Child Care Service             Pet Store  Eastern European Restaurant    English Restaurant  Ethiopian Restaurant           Event Space               Exhibit           Fabric Shop     Falafel Restaurant

In [70]:
onlyclusters[onlyclusters['Cluster Labels']==3]

Neighborhood  Cluster Labels 1st Most Common Venue     2nd Most Common Venue     3rd Most Common Venue          4th Most Common Venue      5th Most Common Venue       6th Most Common Venue    7th Most Common Venue       8th Most Common Venue     9th Most Common Venue         10th Most Common Venue
13              Chiswick             3.0                   Pub                    Bakery                 Bookstore                           Park         Italian Restaurant                 Coffee Shop                     Café                    Platform                Playground                    Supermarket
14            Church End             3.0           Supermarket        Turkish Restaurant       Japanese Restaurant                    Pizza Place                       Café           Indian Restaurant                      Pub                    Pharmacy        Persian Restaurant      Middle Eastern Restaurant
15            Church End             3.0           Supermarket        Turkish Restaurant       Japanese Restaurant                    Pizza Place                       Café           Indian Restaurant                      Pub                    Pharmacy        Persian Restaurant      Middle Eastern Restaurant
16               Clapham             3.0                   Pub              Burger Joint                       Bar                           Café                   Bus Stop               Grocery Store     Gym / Fitness Center                 Coffee Shop                Restaurant            Japanese Restaurant
17           Clerkenwell             3.0                   Pub               Coffee Shop                      Café                          Hotel                Pizza Place                         Bar               Food Truck        Gym / Fitness Center        Italian Restaurant                  Burrito Place
25            Crouch End             3.0                   Pub               Coffee Shop                      Café                       Bus Stop                     Bakery               Grocery Store   Furniture / Home Store             Thai Restaurant      Gym / Fitness Center                      Bookstore
27           Cubitt Town             3.0                  Park                      Café         Indian Restaurant                            Pub                       Farm                       Beach                  Stables                Soccer Field               Supermarket                   Tennis Court
29               Dalston             3.0                   Pub                      Café                Restaurant                           Pool          Convenience Store  Modern European Restaurant                Gastropub                 Coffee Shop      Gym / Fitness Center                    Music Venue
30              Dartford             3.0                   Pub               Supermarket                  Platform                  Grocery Store     Furniture / Home Store              Clothing Store                 Pharmacy                 Coffee Shop                   Theater                         Bakery
39          East Dulwich             3.0                  Café                       Pub         Indian Restaurant                   Burger Joint             Ice Cream Shop               Grocery Store                Gastropub                 Coffee Shop         Convenience Store                       Bus Stop
42            East Sheen             3.0                   Pub               Coffee Shop               Pizza Place                    Supermarket           Stationery Store         Sporting Goods Shop         Business Service                        Café        Chinese Restaurant                       Creperie
44   Elephant and Castle             3.0                   Pub               Pizza Place        Chinese Restaurant                         Garden                       Café                     Theater              Coffee Shop                  Restaurant  Bike Rental / Bike Share 

In [71]:
onlyclusters[onlyclusters['Cluster Labels']==4]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue        3rd Most Common Venue      4th Most Common Venue   5th Most Common Venue     6th Most Common Venue          7th Most Common Venue 8th Most Common Venue 9th Most Common Venue 10th Most Common Venue
1    Blackheath Royal Standard             4.0                   Pub    Chinese Restaurant                Grocery Store                   Bus Stop  Furniture / Home Store                      Café                    Rugby Pitch  Fast Food Restaurant           Zoo Exhibit                   Farm
12                   Chingford             4.0                   Pub                  Café           Italian Restaurant                Coffee Shop           Grocery Store      Fast Food Restaurant  Vegetarian / Vegan Restaurant     Convenience Store           Flea Market                   Farm
31            De Beauvoir Town             4.0                  Café                   Pub         Gym / Fitness Center                Coffee Shop           Deli / Bodega                       Gym                      Gastropub         Garden Center                  Park                  Canal
32                Denmark Hill             4.0           Coffee Shop                   Pub                         Café      Vietnamese Restaurant           Train Station              Optical Shop                  Grocery Store                   Bar     Convenience Store     Chinese Restaurant
41                    East Ham             4.0                   Pub           Coffee Shop            Electronics Store                Supermarket                    Park      Fast Food Restaurant                       Gym Pool       Warehouse Store   Sporting Goods Shop          Grocery Store
53                 Forest Hill             4.0                   Pub           Coffee Shop                         Café                Pizza Place    Gym / Fitness Center                 Gastropub                  Grocery Store             Bookstore         Garden Center          Train Station
58                  Gipsy Hill             4.0                   Pub       Nature Preserve            Indian Restaurant              Train Station                    Café                     Field           Ethiopian Restaurant           Event Space               Exhibit            Fabric Shop
76                     Hanwell             4.0                  Café                   Pub                  Pizza Place                        Gym           Train Station            Discount Store                    Supermarket           Coffee Shop                  Park      Convenience Store
81                Highams Park             4.0           Coffee Shop                   Pub     Mediterranean Restaurant          Indian Restaurant    Cantonese Restaurant         Martial Arts Dojo                    Zoo Exhibit  Ethiopian Restaurant           Event Space                Exhibit
83                    Highgate             4.0                   Pub                Bakery                        Plaza              Memorial Site               Gastropub                      Café                           Pool     Indian Restaurant           Flower Shop         Farmers Market
88                    Homerton             4.0                  Café                   Pub                  Coffee Shop                Supermarket       Convenience Store         Fish & Chips Shop             English Restaurant                   Bar           Art Gallery          Train Station
96                  Kennington             4.0                   Pub                  Café                  Coffee Shop          Indian Restaurant      Italian Restaurant                 Gastropub                         Museum     Fish & Chips Shop           Film Studio      French Restaurant
107                   Ladywell             4.0                   Pub         Deli / Bodega                         Park              Grocery Store             Coffee Shop             

In [72]:
onlyclusters[onlyclusters['Cluster Labels']==5]

Neighborhood  Cluster Labels 1st Most Common Venue       2nd Most Common Venue      3rd Most Common Venue 4th Most Common Venue    5th Most Common Venue    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue 9th Most Common Venue       10th Most Common Venue
7           Charlton             5.0              Bus Stop               Grocery Store                 Food Truck         Historic Site          Thai Restaurant        Convenience Store        Soccer Stadium             Pet Store           Coffee Shop         Ethiopian Restaurant
38        Earlsfield             5.0         Grocery Store                         Pub            Thai Restaurant                Lounge         Indoor Play Area                 Platform                  Café           Music Venue             Gastropub                          Gym
52       Forest Gate             5.0         Grocery Store        Fast Food Restaurant                       Café                Market                      Pub                 Bus Stop     Fish & Chips Shop         Train Station                Bakery           Miscellaneous Shop
55     Friern Barnet             5.0         Grocery Store          Italian Restaurant          Fish & Chips Shop          Dessert Shop               Food Court        Food & Drink Shop  Ethiopian Restaurant           Event Space               Exhibit                   Food Truck
79            Hendon             5.0         Grocery Store          Chinese Restaurant  Middle Eastern Restaurant   Fried Chicken Joint                     Park               Bagel Shop           Coffee Shop    Turkish Restaurant                  Café                    Irish Pub
90         Horn Park             5.0         Grocery Store                   Pet Store                 Laundromat          Soccer Field              Zoo Exhibit     Fast Food Restaurant  Ethiopian Restaurant           Event Space               Exhibit                  Fabric Shop
100           Kenton             5.0                  Park    Mediterranean Restaurant          Indian Restaurant        Sandwich Place            Metro Station                    Hotel                 Field  Fast Food Restaurant         Grocery Store                  Coffee Shop
104        Kingsbury             5.0         Grocery Store                         Pub                Coffee Shop  Fast Food Restaurant              Snack Place  Fruit & Vegetable Store           Supermarket  Gym / Fitness Center  Herbs & Spices Store                 Dessert Shop
105    Kingston Vale             5.0                   Bar              Sandwich Place              Grocery Store          Soccer Field     Fast Food Restaurant       English Restaurant  Ethiopian Restaurant           Event Space               Exhibit                  Fabric Shop
109       Lea Bridge             5.0       Nature Preserve                        Park               Skating Rink         Grocery Store                      Pub         Currywurst Joint  Fast Food Restaurant  Ethiopian Restaurant           Event Space                      Exhibit
113           Leyton             5.0         Grocery Store                        Park                   Bus Stop                 Hotel               Restaurant                     Farm           Zoo Exhibit  Fast Food Restaurant  Ethiopian Restaurant                  Event Space
127        Maze Hill             5.0         Grocery Store                         Pub          Indian Restaurant                   Bar  South Indian Restaurant                     Café        Scenic Lookout           Coffee Shop     Recreation Center                   Playground
134         Mortlake             5.0                   Pub               Grocery Store        American Restaurant           Golf Course         Tapas Restaurant                     Park           Zoo Exhibit        Farmers Market  Ethiopian Restaurant                  Event Space
153           Osidge             5.0         Grocery Store  Construction &

In [73]:
onlyclusters[onlyclusters['Cluster Labels']==6]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue 6th Most Common Venue 7th Most Common Venue 8th Most Common Venue 9th Most Common Venue 10th Most Common Venue
61      Grahame Park             6.0                  Park            Hobby Shop           Zoo Exhibit     Electronics Store  Ethiopian Restaurant           Event Space               Exhibit           Fabric Shop    Falafel Restaurant                   Farm
69   Hackney Marshes             6.0                  Park            Bike Trail           Zoo Exhibit   Filipino Restaurant           Event Space               Exhibit           Fabric Shop    Falafel Restaurant                  Farm         Farmers Market
117    Little Ilford             6.0                  Park           Zoo Exhibit                 Field  Ethiopian Restaurant           Event Space               Exhibit           Fabric Shop    Falafel Restaurant                  Farm         Farmers Market

In [74]:
onlyclusters[onlyclusters['Cluster Labels']==7]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue 6th Most Common Venue 7th Most Common Venue 8th Most Common Venue 9th Most Common Venue 10th Most Common Venue
150  Oakleigh Park             7.0                  Café           Pet Service     Electronics Store  Ethiopian Restaurant           Event Space               Exhibit           Fabric Shop    Falafel Restaurant                  Farm         Farmers Market
260  Woodside Park             7.0                  Café         Grocery Store         Metro Station                 Hotel   Filipino Restaurant           Event Space               Exhibit           Fabric Shop    Falafel Restaurant                   Farm

In [75]:
onlyclusters[onlyclusters['Cluster Labels']==8]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue   3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  6th Most Common Venue     7th Most Common Venue   8th Most Common Venue      9th Most Common Venue     10th Most Common Venue
9        Childs Hill             8.0   Sporting Goods Shop              Bus Stop           Grocery Store            Coffee Shop        Breakfast Spot             Food Truck                Food Court    Fast Food Restaurant                Event Space                    Exhibit
19     Colliers Wood             8.0           Coffee Shop         Grocery Store          Clothing Store                  Hotel  Fast Food Restaurant  Portuguese Restaurant          Department Store                    Park  Middle Eastern Restaurant                Supermarket
22       Cricklewood             8.0           Coffee Shop              Bus Stop    Fast Food Restaurant                  Hotel         Grocery Store                    Pub                      Café    Gym / Fitness Center         Italian Restaurant                Music Store
23      Crofton Park             8.0         Grocery Store           Coffee Shop       Convenience Store                   Café                   Bar           Gourmet Shop             Train Station                 Theater     Furniture / Home Store           Malay Restaurant
40     East Finchley             8.0           Coffee Shop                  Café                     Pub          Grocery Store              Bus Stop               Platform       Japanese Restaurant        Sushi Restaurant                  Bookstore                        Spa
43          Edmonton             8.0    Turkish Restaurant                  Café           Grocery Store       Kebab Restaurant           Supermarket                   Park               Coffee Shop    Fast Food Restaurant       Ethiopian Restaurant                Event Space
59     Golders Green             8.0         Grocery Store           Coffee Shop       Korean Restaurant                   Café      Sushi Restaurant     Turkish Restaurant      Fast Food Restaurant  Shabu-Shabu Restaurant         Falafel Restaurant           Stationery Store
66       Gunnersbury             8.0           Coffee Shop                  Café     Japanese Restaurant   Gym / Fitness Center                   Pub                   Park            Sandwich Place       Electronics Store                   Bus Stop        Sporting Goods Shop
78         Harringay             8.0    Turkish Restaurant                  Café                     Pub                 Bakery           Coffee Shop     Italian Restaurant                  Bus Stop                 Butcher            Organic Grocery  Middle Eastern Restaurant
121       Maida Vale             8.0                  Café           Pizza Place           Deli / Bodega            Coffee Shop       Thai Restaurant    Japanese Restaurant        Athletics & Sports                     Gym              Grocery Store              Metro Station
123       Manor Park             8.0         Grocery Store                  Café              Beer Store    Sporting Goods Shop           Coffee Shop           Skating Rink     Vietnamese Restaurant             Supermarket                  Gastropub         Chinese Restaurant
139        New Cross             8.0                  Café           Coffee Shop           Grocery Store                    Pub          Cocktail Bar              Gastropub       Lebanese Restaurant                     Bar                    Theater            Thai Restaurant
141    New Southgate             8.0         Grocery Store   Sporting Goods Shop  Furniture / Home Store         Hardware Store             Pet Store         Shopping Plaza      Fast Food Restaurant                    Café                Coffee Shop          Electronics Store
144          Norbury             8.0         Grocery Store                  Café          Breakfast Spot               Pharmacy   

In [76]:
onlyclusters[onlyclusters['Cluster Labels']==9]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue 6th Most Common Venue 7th Most Common Venue 8th Most Common Venue 9th Most Common Venue 10th Most Common Venue
24    Crossness             9.0       Nature Preserve   Filipino Restaurant  Ethiopian Restaurant           Event Space               Exhibit           Fabric Shop    Falafel Restaurant                  Farm        Farmers Market   Fast Food Restaurant

In [77]:
onlyclusters[onlyclusters['Cluster Labels']==10]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue 6th Most Common Venue 7th Most Common Venue 8th Most Common Venue 9th Most Common Venue 10th Most Common Venue
228  Upper Norwood            10.0    English Restaurant   Filipino Restaurant  Ethiopian Restaurant           Event Space               Exhibit           Fabric Shop    Falafel Restaurant                  Farm        Farmers Market   Fast Food Restaurant

In [78]:
onlyclusters[onlyclusters['Cluster Labels']==11]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue      3rd Most Common Venue      4th Most Common Venue          5th Most Common Venue   6th Most Common Venue   7th Most Common Venue         8th Most Common Venue      9th Most Common Venue     10th Most Common Venue
2         Brent Cross            11.0        Clothing Store           Coffee Shop                       Café           Department Store                  Women's Store             Supermarket             Men's Store             Electronics Store                 Shoe Store          Accessories Store
3          Brent Park            11.0           Coffee Shop                 Hotel                Supermarket                 Food Court              Electronics Store        Pedestrian Plaza                Platform                          Café               Burger Joint                 Sports Bar
5          Chalk Farm            11.0                  Café                   Bar         Italian Restaurant                Coffee Shop                            Pub             Pizza Place                  Bakery                          Park             Breakfast Spot                Music Venue
6       Charing Cross            11.0                 Hotel                   Pub               Cocktail Bar             Ice Cream Shop                   Burger Joint                  Bakery                   Plaza                    Steakhouse                Art Gallery                 Restaurant
8             Chelsea            11.0                Bakery                   Pub          French Restaurant         English Restaurant                           Park            Burger Joint          Ice Cream Shop              Department Store                        Spa           Tapas Restaurant
10          Chinatown            11.0               Theater        Ice Cream Shop                      Hotel                      Plaza                         Bakery             Coffee Shop                     Pub                    Comic Shop        Arts & Crafts Store                 Steakhouse
21      Covent Garden            11.0           Coffee Shop            Restaurant               Cocktail Bar                    Theater                            Pub                   Hotel              Steakhouse                Ice Cream Shop               Burger Joint                Opera House
28       Custom House            11.0                 Hotel        Scenic Lookout                  Hotel Bar                     Garden           Gym / Fitness Center             Coffee Shop          History Museum                        Castle          French Restaurant              Grocery Store
33           Deptford            11.0                   Pub                 Hotel       Gym / Fitness Center                Coffee Shop                  Grocery Store                     Bar     Japanese Restaurant            Athletics & Sports      Vietnamese Restaurant               Cocktail Bar
35            Dulwich            11.0             Gastropub            Restaurant                       Park               Tennis Court                    Art Gallery    Gym / Fitness Center             Flower Shop                   Fish Market         Falafel Restaurant                 Food Court
36             Ealing            11.0           Coffee Shop                   Pub             Clothing Store                   Platform                   Burger Joint                    Park                    Café                        Bakery                Pizza Place       Fast Food Restaurant
37        Earls Court            11.0                 Hotel                  Café                     Garden                        Pub            Lebanese Restaurant             Pizza Place         Thai Restaurant                   Coffee Shop              Grocery Store              Historic Site
46         Falconwood            11.0     Other Repair Shop    Miscellaneous Shop           Motorsports Shop              

In [79]:
onlyclusters[onlyclusters['Cluster Labels']==12]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue 6th Most Common Venue 7th Most Common Venue 8th Most Common Venue 9th Most Common Venue 10th Most Common Venue
0       Barnet Gate            12.0                Forest          Soccer Field                   Pub         Indie Theater  Fast Food Restaurant     Electronics Store    English Restaurant  Ethiopian Restaurant           Event Space                Exhibit
180  Shooter's Hill            12.0                   Pub                  Café                Forest            Food Stand    English Restaurant  Ethiopian Restaurant           Event Space               Exhibit           Fabric Shop     Falafel Restaurant
213   Sydenham Hill            12.0                Forest                   Pub                  Park  Fast Food Restaurant    English Restaurant  Ethiopian Restaurant           Event Space               Exhibit           Fabric Shop     Falafel Restaurant

In [80]:
onlyclusters[onlyclusters['Cluster Labels']==13]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue        3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue 6th Most Common Venue 7th Most Common Venue 8th Most Common Venue 9th Most Common Venue 10th Most Common Venue
129  Middle Park            13.0        Scenic Lookout           Zoo Exhibit  Eastern European Restaurant    English Restaurant  Ethiopian Restaurant           Event Space               Exhibit           Fabric Shop    Falafel Restaurant                   Farm

In [81]:
onlyclusters[onlyclusters['Cluster Labels']==14]

Empty DataFrame
Columns: [Neighborhood, Cluster Labels, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue]
Index: []